In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.pipeline import Pipeline
import warnings
warnings.filterwarnings('ignore')

In [ ]:
!pip install prophet dagshub scikit-learn pandas "numpy<2.0" mlflow pyarrow==14.0.1 neuralforecast

In [ ]:
import mlflow
import mlflow.sklearn
import dagshub
import os

os.environ['MLFLOW_TRACKING_USERNAME'] = 'nipkha21'
os.environ['MLFLOW_TRACKING_PASSWORD'] = '202fb8a4c58a90b0eb3598b1037498eb6fe9f593'

dagshub.init(repo_owner='TomC333', repo_name='ml-walmart-recruiting', mlflow=True)
mlflow.set_tracking_uri('https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow')

❗❗❗ AUTHORIZATION REQUIRED ❗❗❗

Output()



Open the following link in your browser to authorize the client:
https://dagshub.com/login/oauth/authorize?state=e712278c-fe86-4f5a-8375-17fef780fd61&client_id=32b60ba385aa7cecf24046d8195a71c07dd345d9657977863b52e7748e0f0f28&middleman_request_id=e4ffd2720c38f45b1b16bc9350d960f6acddbd8317a9777e5e6ea154b382a41c




Accessing as nipkha21

Initialized MLflow to track repo "TomC333/ml-walmart-recruiting"

Repository TomC333/ml-walmart-recruiting initialized!

In [ ]:
try:
    from neuralforecast import NeuralForecast
    from neuralforecast.models import NBEATS
except ImportError:
    print("Installing neuralforecast...")
    import subprocess
    subprocess.check_call(["pip", "install", "neuralforecast"])
    from neuralforecast import NeuralForecast
    from neuralforecast.models import NBEATS

import torch

print("Setup complete!")

Setup complete!


In [ ]:
train = pd.read_csv('train.csv')
test = pd.read_csv('test.csv')

print(f"Train shape: {train.shape}")
print(f"Test shape: {test.shape}")

print("\nTrain data sample:")
print(train.head())
print(f"\nWeekly_Sales stats:")
print(train['Weekly_Sales'].describe())

train['Date'] = pd.to_datetime(train['Date'])
test['Date'] = pd.to_datetime(test['Date'])

print(f"\nDate Analysis:")
print(f"Training data date range: {train['Date'].min()} to {train['Date'].max()}")
print(f"Test data date range: {test['Date'].min()} to {test['Date'].max()}")
print(f"Gap between train and test: {(test['Date'].min() - train['Date'].max()).days} days")

print(f"\nData structure:")
print(f"Training: {train['Store'].nunique()} stores, {train['Dept'].nunique()} departments")
print(f"Test: {test['Store'].nunique()} stores, {test['Dept'].nunique()} departments")
print(f"Training series: {len(train.groupby(['Store', 'Dept']))}")
print(f"Test series: {len(test.groupby(['Store', 'Dept']))}")

train_series = set(zip(train['Store'], train['Dept']))
test_series = set(zip(test['Store'], test['Dept']))
common_series = train_series.intersection(test_series)
print(f"Common Store-Dept combinations: {len(common_series)}")
print(f"Test-only series: {len(test_series - train_series)}")
print(f"Train-only series: {len(train_series - test_series)}")

if len(test_series - train_series) > 0:
    print("WARNING: Test set contains Store-Dept combinations not seen in training!")
    print("This will cause prediction issues.")

Train shape: (421570, 5)
Test shape: (115064, 4)

Train data sample:
   Store  Dept        Date  Weekly_Sales  IsHoliday
0      1     1  2010-02-05      24924.50      False
1      1     1  2010-02-12      46039.49       True
2      1     1  2010-02-19      41595.55      False
3      1     1  2010-02-26      19403.54      False
4      1     1  2010-03-05      21827.90      False

Weekly_Sales stats:
count    421570.000000
mean      15981.258123
std       22711.183519
min       -4988.940000
25%        2079.650000
50%        7612.030000
75%       20205.852500
max      693099.360000
Name: Weekly_Sales, dtype: float64

Date Analysis:
Training data date range: 2010-02-05 00:00:00 to 2012-10-26 00:00:00
Test data date range: 2012-11-02 00:00:00 to 2013-07-26 00:00:00
Gap between train and test: 7 days

Data structure:
Training: 45 stores, 81 departments
Test: 45 stores, 81 departments
Training series: 3331
Test series: 3169
Common Store-Dept combinations: 3158
Test-only series: 11
Train-only 

In [ ]:
class SimpleNBEATSPreprocessor(BaseEstimator, TransformerMixin):
    """
    Turns train/test tables into [unique_id, ds, y, IsHoliday] for NeuralForecast N-BEATS.
    Uses only Store, Dept, Date, Weekly_Sales (or zeros if missing).
    Drops all exogenous features.
    """
    def fit(self, X, y=None):
        return self

    def transform(self, X):
        df = X.copy()
        df['Date'] = pd.to_datetime(df['Date'])
        if 'Weekly_Sales' in df.columns:
            df['y'] = df['Weekly_Sales']
        else:
            df['y'] = 0.0
        df['unique_id'] = df['Dept'].astype(str) + '_' + df['Store'].astype(str)
        df = df.rename(columns={'Date': 'ds'})
        return df[['unique_id', 'ds', 'y', 'IsHoliday']]

In [ ]:
def create_train_val_split(df, split_date='2012-02-15'):
    """Split data into train and validation sets based on date"""
    df = df.copy()
    df['Date'] = pd.to_datetime(df['Date'])

    train_mask = df['Date'] < pd.to_datetime(split_date)
    val_mask = df['Date'] >= pd.to_datetime(split_date)

    train_df = df[train_mask].copy()
    val_df = df[val_mask].copy()

    return train_df, val_df

train_data, val_data = create_train_val_split(train)

print(f"Training data: {train_data.shape[0]} rows")
print(f"Validation data: {val_data.shape[0]} rows")
print(f"Training period: {train_data['Date'].min()} to {train_data['Date'].max()}")
print(f"Validation period: {val_data['Date'].min()} to {val_data['Date'].max()}")

Training data: 311960 rows
Validation data: 109610 rows
Training period: 2010-02-05 00:00:00 to 2012-02-10 00:00:00
Validation period: 2012-02-17 00:00:00 to 2012-10-26 00:00:00


In [ ]:
def split_sales_data(df: pd.DataFrame, split_date: pd.Timestamp = pd.Timestamp('2012-02-15')):
    """
    Splits sales data into train and test sets based on a provided date,
    including the 'Weekly_Sales' column in both dataframes.
    Parameters:
    - df (pd.DataFrame): df to be split.
    - split_date (pd.Timestamp): The cutoff date for train-test split.
    Returns:
    - df_train, df_test: Tuple of training and test dataframes including 'Weekly_Sales'.
    """
    df = df.copy()
    df['Date'] = pd.to_datetime(df['Date'])
    train_mask = df['Date'] < split_date
    test_mask = df['Date'] >= split_date
    df_train = df[train_mask].copy()
    df_test = df[test_mask].copy()
    return df_train, df_test

In [ ]:
train_df, val_df = split_sales_data(train)

preprocessor = SimpleNBEATSPreprocessor()
train_df = preprocessor.fit_transform(train_df)
val_df = preprocessor.transform(val_df)

w_train = train_df["IsHoliday"].map({True: 5, False: 1}).values
w_val = val_df["IsHoliday"].map({True: 5, False: 1}).values
train_df = train_df.drop('IsHoliday', axis=1)
val_df = val_df.drop('IsHoliday', axis=1)

X_train = train_df.drop('y', axis=1)
y_train = train_df['y']
X_val = val_df.drop('y', axis=1)
y_val = val_df['y']

In [ ]:
def weighted_mae(y_true, y_pred, weights):
    """Weighted Mean Absolute Error (holidays weighted 5x)"""
    mask = np.isfinite(y_true) & np.isfinite(y_pred) & np.isfinite(weights)
    if not mask.any() or weights[mask].sum() == 0:
        return np.nan

    y_true_clean = y_true[mask]
    y_pred_clean = y_pred[mask]
    weights_clean = weights[mask]

    return (weights_clean * np.abs(y_true_clean - y_pred_clean)).sum() / weights_clean.sum()

def calculate_metrics(y_true, y_pred, weights=None):
    """Calculate comprehensive evaluation metrics"""
    if weights is None:
        weights = np.ones_like(y_true)

    metrics = {
        'WMAE': weighted_mae(y_true, y_pred, weights),
        'MAE': mean_absolute_error(y_true, y_pred),
        'RMSE': np.sqrt(mean_squared_error(y_true, y_pred)),
        'R2': r2_score(y_true, y_pred)
    }
    return metrics

def plot_predictions(y_true, y_pred, title="Predictions vs Actual", sample_size=5000):
    """Plot actual vs predicted values"""
    if len(y_true) > sample_size:
        indices = np.random.choice(len(y_true), sample_size, replace=False)
        y_true_sample = y_true[indices]
        y_pred_sample = y_pred[indices]
    else:
        y_true_sample = y_true
        y_pred_sample = y_pred

    plt.figure(figsize=(10, 6))
    plt.subplot(1, 2, 1)
    plt.scatter(y_true_sample, y_pred_sample, alpha=0.5, s=1)
    plt.plot([y_true_sample.min(), y_true_sample.max()],
             [y_true_sample.min(), y_true_sample.max()], 'r--', lw=2)
    plt.xlabel('Actual')
    plt.ylabel('Predicted')
    plt.title(f'{title} - Scatter Plot')

    plt.subplot(1, 2, 2)
    residuals = y_true_sample - y_pred_sample
    plt.scatter(y_pred_sample, residuals, alpha=0.5, s=1)
    plt.axhline(y=0, color='r', linestyle='--')
    plt.xlabel('Predicted')
    plt.ylabel('Residuals')
    plt.title('Residuals Plot')

    plt.tight_layout()
    return plt.gcf()


In [ ]:
import torch
from neuralforecast.models import NBEATS

class CustomNBEATS(NBEATS):
    """Custom N-BEATS with proper optimizer configuration"""

    def __init__(self, learning_rate=0.001, *args, **kwargs):
        super().__init__(*args, **kwargs)
        self.learning_rate = learning_rate

    def configure_optimizers(self):
        optimizer = torch.optim.AdamW(self.parameters(), lr=self.learning_rate)
        scheduler = torch.optim.lr_scheduler.StepLR(optimizer, step_size=10, gamma=0.9)
        return {
            "optimizer": optimizer,
            "lr_scheduler": {
                "scheduler": scheduler,
                "interval": "epoch",
                "frequency": 1
            }
        }

class NBEATSModel(BaseEstimator, TransformerMixin):
    """
    Wrapper for N-BEATS model that follows sklearn interface
    """

    def __init__(self,
                 input_size=52,
                 h=40,
                 max_steps=2000,
                 batch_size=64,
                 stack_types=["identity", "trend", "seasonality"],
                 n_blocks=[3, 3, 3],
                 n_polynomials=2,
                 n_harmonics=2,
                 learning_rate=0.001,
                 random_seed=42):

        self.input_size = input_size
        self.h = h
        self.max_steps = max_steps
        self.batch_size = batch_size
        self.stack_types = stack_types
        self.n_blocks = n_blocks
        self.n_polynomials = n_polynomials
        self.n_harmonics = n_harmonics
        self.learning_rate = learning_rate
        self.random_seed = random_seed
        self.nf = None
        self.is_fitted = False

    def fit(self, X, y=None):
      """Fit the N-BEATS model"""
      if not self.is_fitted:
          if isinstance(X, pd.DataFrame) and 'y' in X.columns:
              df = X.copy()
          elif y is not None:
              df = X.copy()
              df['y'] = y
          else:
              raise ValueError("Either X should have 'y' column or y should be provided separately")

          df = df.sort_values(['unique_id', 'ds']).reset_index(drop=True)

          series_lengths = df.groupby('unique_id').size()
          min_length = series_lengths.min()
          print(f"Minimum series length: {min_length}")
          print(f"Input size requirement: {self.input_size}")

          device = "gpu" if torch.cuda.is_available() else "cpu"

          model = CustomNBEATS(
              input_size=self.input_size,
              h=self.h,
              max_steps=self.max_steps,
              batch_size=self.batch_size,
              stack_types=self.stack_types,
              n_blocks=self.n_blocks,
              n_polynomials=self.n_polynomials,
              n_harmonics=self.n_harmonics,
              learning_rate=self.learning_rate,
              random_seed=self.random_seed,
              accelerator=device,
              devices=1,
              logger=False,
              enable_progress_bar=True,
              enable_model_summary=False
          )

          self.nf = NeuralForecast(models=[model], freq='W-FRI')

          print(f"Fitting N-BEATS model with {df['unique_id'].nunique()} series...")
          print(f"Total data points: {len(df)}")

          self.nf.fit(df)
          self.is_fitted = True

      return self

    def predict(self, X=None):
      """Generate predictions for the input data X"""
      print(f"predict() called with X={'None' if X is None else 'Data'}")

      if not self.is_fitted:
          raise ValueError("Model must be fitted before making predictions")

      if X is not None:
          print(f"Input X shape: {X.shape}")
          print(f"Input X columns: {X.columns.tolist()}")

          real = pd.DataFrame({"unique_id": X["unique_id"], "ds": X["ds"], "y": X["y"]})
          print(f"Real shape: {real.shape}")

          preds = self.nf.predict()
          print(f"Preds shape: {preds.shape}")
          print(f"Preds columns: {preds.columns.tolist()}")

          merged = real.merge(preds, on=["unique_id", "ds"], how="left").fillna(0)
          print(f"Merged shape: {merged.shape}")
          print(f"Merged columns: {merged.columns.tolist()}")

          return merged
      else:
          print("Taking default path - returning all predictions")
          return self.nf.predict()
    def predict_specific_dates(self, target_dates_df):
      """
      Predict for specific dates by using the closest predictions (vectorized)
      target_dates_df should have columns: unique_id, ds (target dates)
      """
      if not self.is_fitted:
          raise ValueError("Model must be fitted before making predictions")

      predictions = self.nf.predict()

      pred_cols = [col for col in predictions.columns if 'NBEATS' in col or 'CustomNBEATS' in col]
      pred_col = pred_cols[0]

      target_dates_df = target_dates_df.copy()
      target_dates_df['ds'] = pd.to_datetime(target_dates_df['ds'])
      predictions['ds'] = pd.to_datetime(predictions['ds'])

      target_dates_df['_temp_key'] = 1
      predictions['_temp_key'] = 1

      merged = target_dates_df.merge(predictions, on=['unique_id', '_temp_key'], suffixes=('_target', '_pred'))

      merged['date_diff'] = abs((merged['ds_pred'] - merged['ds_target']).dt.days)

      closest_idx = merged.groupby(['unique_id', 'ds_target'])['date_diff'].idxmin()
      results = merged.loc[closest_idx, ['unique_id', 'ds_target', pred_col]].copy()
      results = results.rename(columns={'ds_target': 'ds'})

      results = results.drop(columns=['_temp_key'], errors='ignore')

      return results.reset_index(drop=True)

def evaluate_model_performance(model, train_data, val_data, model_name="N-BEATS"):
    """Evaluate model performance and return metrics"""

    predictions = model.predict()

    pred_cols = [col for col in predictions.columns if 'NBEATS' in col or 'CustomNBEATS' in col]
    if not pred_cols:
        pred_cols = [col for col in predictions.columns if col not in ['unique_id', 'ds']]

    if not pred_cols:
        raise ValueError("Could not find prediction column in results")

    pred_col = pred_cols[0]
    print(f"Using prediction column: {pred_col}")

    val_with_pred = val_data.merge(
        predictions[['unique_id', 'ds', pred_col]],
        on=['unique_id', 'ds'],
        how='left'
    )

    val_with_pred[pred_col] = val_with_pred[pred_col].fillna(0)

    y_true = val_with_pred['y'].values
    y_pred = val_with_pred[pred_col].values

    print(f"Evaluation summary:")
    print(f"  Total predictions: {len(y_pred)}")
    print(f"  Non-zero predictions: {(y_pred != 0).sum()}")
    print(f"  Prediction range: [{y_pred.min():.2f}, {y_pred.max():.2f}]")
    print(f"  Actual range: [{y_true.min():.2f}, {y_true.max():.2f}]")

    weights = np.ones_like(y_true)

    metrics = calculate_metrics(y_true, y_pred, weights)

    return metrics, y_true, y_pred

def generate_kaggle_submission(model, test_features, original_test):
    """
    model: your trained NBEATSModel
    test_features: DataFrame with columns ['unique_id','ds','y'] (y may be dummy)
    original_test: the original Kaggle test DataFrame with Store, Dept, Date
    """
    preds_df = model.predict(test_features)

    y_pred = preds_df.iloc[:, -1].reset_index(drop=True)

    submission = pd.DataFrame({
        "Id": original_test["Store"].astype(str)
              + "_" + original_test["Dept"].astype(str)
              + "_" + original_test["Date"].astype(str),
        "Weekly_Sales": y_pred
    })

    return submission

In [ ]:
my_params = {
    'input_size': 20,
    'h': 24,
    'max_steps': 1500,
    'batch_size': 64,
    'stack_types': ["identity", "trend", "seasonality"],
    'n_blocks': [1,1,1],
    'n_polynomials': 2,
    'n_harmonics': 2,
    'learning_rate': 0.001,
    'random_seed': 42
}
best_params = {
    'input_size': 52,
    'h': 40,
    'max_steps': 2000,
    'batch_size': 64,
    'stack_types': ["identity", "trend", "seasonality"],
    'n_blocks': [3,3,3],
    'n_polynomials': 2,
    'n_harmonics': 2,
    'learning_rate': 0.001,
    'random_seed': 42
}

In [ ]:
def calculate_required_horizon(train_data, test_data):
    """Calculate the actual horizon needed based on train-test gap"""

    train_end = train_data['Date'].max()
    test_start = test_data['Date'].min()
    test_end = test_data['Date'].max()

    weeks_to_start = ((test_start - train_end).days // 7) + 1
    weeks_to_end = ((test_end - train_end).days // 7) + 1

    print(f"Gap analysis:")
    print(f"  Training ends: {train_end}")
    print(f"  Test starts: {test_start}")
    print(f"  Test ends: {test_end}")
    print(f"  Weeks to test start: {weeks_to_start}")
    print(f"  Weeks to test end: {weeks_to_end}")
    print(f"  Required horizon: {weeks_to_end}")

    return weeks_to_end

required_h = calculate_required_horizon(train, test)

adjusted_params = best_params.copy()
if required_h > 50:
    print(f"Gap too large ({required_h} weeks), keeping h=40")
    adjusted_params['h'] = 40
else:
    print(f"Using calculated horizon: {required_h}")
    adjusted_params['h'] = max(required_h, 40)

print(f"Final parameters: h={adjusted_params['h']}")

Gap analysis:
  Training ends: 2012-10-26 00:00:00
  Test starts: 2012-11-02 00:00:00
  Test ends: 2013-07-26 00:00:00
  Weeks to test start: 2
  Weeks to test end: 40
  Required horizon: 40
Using calculated horizon: 40
Final parameters: h=40


In [ ]:
print(f"Using adjusted parameters: {adjusted_params}")

mlflow.set_experiment("NBEATS_Training")

with mlflow.start_run(run_name="NBEATS_Config_Adjusted"):

    mlflow.log_params(adjusted_params)

    model = NBEATSModel(**adjusted_params)
    model.fit(train_df)

    metrics, y_true, y_pred = evaluate_model_performance(model, train_df, val_df)

    for metric, value in metrics.items():
        mlflow.log_metric(f"val_{metric}", value)

    print(f"\nValidation Metrics:")
    for metric, value in metrics.items():
        print(f"  {metric}: {value:.4f}")

    fig = plot_predictions(y_true, y_pred, "Validation Set Config")
    mlflow.log_figure(fig, "validation_predictions.png")
    plt.close(fig)

    if metrics['WMAE'] < 5000:
        print(f"\nModel performance looks good (WMAE: {metrics['WMAE']:.2f}). Generating submission...")

        full_train_processed = preprocessor.transform(train)
        final_model = NBEATSModel(**adjusted_params)
        final_model.fit(full_train_processed)

        test_processed = preprocessor.transform(test)

        submission = generate_kaggle_submission(final_model, test_processed, test)

        submission.to_csv('nbeats_submission.csv', index=False)

        print(f"\nSubmission generated successfully!")
        print(f"Submission shape: {submission.shape}")
        print("Submission sample:")
        print(submission.head(10))
        print(f"Submission stats:")
        print(f"  Min: {submission['Weekly_Sales'].min():.2f}")
        print(f"  Max: {submission['Weekly_Sales'].max():.2f}")
        print(f"  Mean: {submission['Weekly_Sales'].mean():.2f}")
        print(f"  Non-zero predictions: {(submission['Weekly_Sales'] != 0).sum()} / {len(submission)}")

        print(f"\nSubmission validation:")
        print(f"  Expected length (from test): {len(test)}")
        print(f"  Actual length: {len(submission)}")
        print(f"  ID format check: {submission['Id'].iloc[0]}")

        if submission['Weekly_Sales'].isnull().sum() > 0:
            print(f"  WARNING: {submission['Weekly_Sales'].isnull().sum()} null predictions!")

        if (submission['Weekly_Sales'] == 0).sum() > len(submission) * 0.5:
            print(f"  WARNING: {(submission['Weekly_Sales'] == 0).sum()} zero predictions ({(submission['Weekly_Sales'] == 0).sum()/len(submission)*100:.1f}%)!")

        print(f"\nAdvanced diagnostics:")

        predictions_raw = final_model.predict()
        pred_date_range = (predictions_raw['ds'].min(), predictions_raw['ds'].max())
        test_date_range = (test_processed['ds'].min(), test_processed['ds'].max())

        print(f"  Model prediction date range: {pred_date_range[0]} to {pred_date_range[1]}")
        print(f"  Test date range: {test_date_range[0]} to {test_date_range[1]}")

        overlap_start = max(pred_date_range[0], test_date_range[0])
        overlap_end = min(pred_date_range[1], test_date_range[1])

        if overlap_start <= overlap_end:
            print(f"  Date overlap exists: {overlap_start} to {overlap_end}")
        else:
            print(f"  WARNING: No date overlap! This explains the poor Kaggle score.")
            print(f"  Prediction ends: {pred_date_range[1]}")
            print(f"  Test starts: {test_date_range[0]}")
            print(f"  Gap: {(test_date_range[0] - pred_date_range[1]).days} days")

        mlflow.log_artifact('nbeats_submission.csv')

    else:
        print(f"Model performance not satisfactory (WMAE: {metrics['WMAE']:.2f}). Skipping submission generation.")

print("\n" + "="*60)
print("EXPERIMENT COMPLETE")
print("="*60)

Using adjusted parameters: {'input_size': 52, 'h': 40, 'max_steps': 2000, 'batch_size': 64, 'stack_types': ['identity', 'trend', 'seasonality'], 'n_blocks': [3, 3, 3], 'n_polynomials': 2, 'n_harmonics': 2, 'learning_rate': 0.001, 'random_seed': 42}


INFO:lightning_fabric.utilities.seed:Seed set to 42
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Minimum series length: 1
Input size requirement: 52
Fitting N-BEATS model with 3309 series...
Total data points: 311960
Using parameters:
  input_size: 52
  h: 40
  max_steps: 2000
  batch_size: 64
  stack_types: ['identity', 'trend', 'seasonality']
  n_blocks: [3, 3, 3]


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

...

Preds shape: (133240, 3)
Preds columns: ['unique_id', 'ds', 'CustomNBEATS']
Merged shape: (115064, 4)
Merged columns: ['unique_id', 'ds', 'y', 'CustomNBEATS']


INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]



Submission generated successfully!
Submission shape: (115064, 2)
Submission sample:
               Id  Weekly_Sales
0  1_1_2012-11-02  30405.783203
1  1_1_2012-11-09  22148.367188
2  1_1_2012-11-16  20392.451172
3  1_1_2012-11-23  21678.683594
4  1_1_2012-11-30  21553.025391
5  1_1_2012-12-07  30858.140625
6  1_1_2012-12-14  37502.843750
7  1_1_2012-12-21  43389.398438
8  1_1_2012-12-28  26629.292969
9  1_1_2013-01-04  19514.703125
Submission stats:
  Min: -4038.17
  Max: 521123.06
  Mean: 16722.54
  Non-zero predictions: 114718 / 115064

Submission validation:
  Expected length (from test): 115064
  Actual length: 115064
  ID format check: 1_1_2012-11-02

Advanced diagnostics:
predict() called with X=None
Taking default path - returning all predictions


Predicting: |          | 0/? [00:00<?, ?it/s]

  Model prediction date range: 2010-02-12 00:00:00 to 2013-08-02 00:00:00
  Test date range: 2012-11-02 00:00:00 to 2013-07-26 00:00:00
  Date overlap exists: 2012-11-02 00:00:00 to 2013-07-26 00:00:00
Model registered in MLflow Model Registry!
🏃 View run NBEATS_Config_Adjusted at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/19/runs/ee77dc6605b94f8da368eb2163011b28
🧪 View experiment at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/19

EXPERIMENT COMPLETE


In [ ]:
submission.head(100)

Id  Weekly_Sales
0   1_1_2012-11-02  51922.429688
1   1_1_2012-11-09  34697.281250
2   1_1_2012-11-16  36088.339844
3   1_1_2012-11-23  37366.542969
4   1_1_2012-11-30  48805.906250
..             ...           ...
95  1_3_2013-03-01  30989.462891
96  1_3_2013-03-08  30119.396484
97  1_3_2013-03-15  31311.970703
98  1_3_2013-03-22  30962.722656
99  1_3_2013-03-29  33306.054688

[100 rows x 2 columns]

In [ ]:
baseline_params = {
    'input_size': 20,
    'h': 24,
    'max_steps': 1500,
    'batch_size': 64,
    'stack_types': ["identity", "trend", "seasonality"],
    'n_blocks': [1,1,1],
    'n_polynomials': 2,
    'n_harmonics': 2,
    'learning_rate': 0.001,
    'random_seed': 42
}

best_params = {
    'input_size': 52,
    'h': 40,
    'max_steps': 2000,
    'batch_size': 64,
    'stack_types': ["identity", "trend", "seasonality"],
    'n_blocks': [3, 3, 3],
    'n_polynomials': 2,
    'n_harmonics': 2,
    'learning_rate': 0.001,
    'random_seed': 42
}

In [ ]:
def run_experiment(params, experiment_name, run_name):
    """Run a single hyperparameter experiment"""

    mlflow.set_experiment(experiment_name)

    with mlflow.start_run(run_name=run_name):
        mlflow.log_params(params)

        model = NBEATSModel(**params)
        model.fit(X_train, y_train)

        val_data_with_y = X_val.copy()
        val_data_with_y['y'] = y_val.values

        preds_df = model.predict(val_data_with_y)
        pred_col = preds_df.columns[-1]
        y_pred = preds_df[pred_col].values

        weights = w_val
        metrics = calculate_metrics(y_val.values, y_pred, weights)

        # Log metrics
        for metric, value in metrics.items():
            mlflow.log_metric(f"val_{metric}", value)

        print(f"{run_name}: WMAE = {metrics['WMAE']:.2f}")

        return metrics['WMAE'], model

best_wmae = float('inf')
best_params_found = baseline_params.copy()
best_model = None

In [ ]:
print("\n1. Testing Input Sizes...")
input_sizes = [26, 52, 78, 104]

for input_size in input_sizes:
    params = baseline_params.copy()
    params['input_size'] = input_size

    val_wmae, model = run_experiment(
        params,
        "NBEATS_Hyperparameter_Tuning",
        f"InputSize_{input_size}"
    )

    if val_wmae < best_wmae:
        best_wmae = val_wmae
        best_params_found = params.copy()
        best_model = model
        print(f"  → New best! WMAE: {val_wmae:.2f}")


1. Testing Input Sizes...


INFO:lightning_fabric.utilities.seed:Seed set to 42
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Minimum series length: 1
Input size requirement: 26
Fitting N-BEATS model with 3309 series...
Total data points: 311960


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_steps=1500` reached.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


predict() called with X=Data
Input X shape: (109610, 3)
Input X columns: ['unique_id', 'ds', 'y']
Real shape: (109610, 3)


Predicting: |          | 0/? [00:00<?, ?it/s]

Preds shape: (79416, 3)
Preds columns: ['unique_id', 'ds', 'CustomNBEATS']
Merged shape: (109610, 4)
Merged columns: ['unique_id', 'ds', 'y', 'CustomNBEATS']
InputSize_104: WMAE = 10520.38
🏃 View run InputSize_104 at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/22/runs/cd2a4f1a3a40414b83e095c00bc0cced
🧪 View experiment at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/22


In [ ]:
best_params_found

{'input_size': 52,
 'h': 24,
 'max_steps': 1500,
 'batch_size': 64,
 'stack_types': ['identity', 'trend', 'seasonality'],
 'n_blocks': [1, 1, 1],
 'n_polynomials': 2,
 'n_harmonics': 2,
 'learning_rate': 0.001,
 'random_seed': 42}

In [ ]:
print("\n2. Testing Horizons...")
horizons = [24, 32, 40, 48]

for h in horizons:
    params = best_params_found.copy()
    params['h'] = h

    val_wmae, model = run_experiment(
        params,
        "NBEATS_Hyperparameter_Tuning",
        f"Horizon_{h}"
    )

    if val_wmae < best_wmae:
        best_wmae = val_wmae
        best_params_found = params.copy()
        best_model = model
        print(f"  → New best! WMAE: {val_wmae:.2f}")


2. Testing Horizons...


INFO:lightning_fabric.utilities.seed:Seed set to 42
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Minimum series length: 1
Input size requirement: 52
Fitting N-BEATS model with 3309 series...
Total data points: 311960


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_steps=1500` reached.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


predict() called with X=Data
Input X shape: (109610, 3)
Input X columns: ['unique_id', 'ds', 'y']
Real shape: (109610, 3)


Predicting: |          | 0/? [00:00<?, ?it/s]

Preds shape: (158832, 3)
Preds columns: ['unique_id', 'ds', 'CustomNBEATS']
Merged shape: (109610, 4)
Merged columns: ['unique_id', 'ds', 'y', 'CustomNBEATS']
Horizon_48: WMAE = 1632.61
🏃 View run Horizon_48 at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/22/runs/cb7a565d81ef414b83de37fc3c0abddb
🧪 View experiment at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/22


In [ ]:
best_params_found

{'input_size': 52,
 'h': 40,
 'max_steps': 1500,
 'batch_size': 64,
 'stack_types': ['identity', 'trend', 'seasonality'],
 'n_blocks': [1, 1, 1],
 'n_polynomials': 2,
 'n_harmonics': 2,
 'learning_rate': 0.001,
 'random_seed': 42}

In [ ]:
print("\n3. Testing Block Configurations...")
block_configs = [
    [2, 2, 2],
    [3, 3, 3],
    [4, 4, 4],
    [2, 3, 4],
    [5, 5, 5]
]

for n_blocks in block_configs:
    params = best_params_found.copy()
    params['n_blocks'] = n_blocks

    val_wmae, model = run_experiment(
        params,
        "NBEATS_Hyperparameter_Tuning",
        f"Blocks_{'_'.join(map(str, n_blocks))}"
    )

    if val_wmae < best_wmae:
        best_wmae = val_wmae
        best_params_found = params.copy()
        best_model = model
        print(f"  → New best! WMAE: {val_wmae:.2f}")


3. Testing Block Configurations...


INFO:lightning_fabric.utilities.seed:Seed set to 42
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Minimum series length: 1
Input size requirement: 52
Fitting N-BEATS model with 3309 series...
Total data points: 311960


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_steps=1500` reached.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


predict() called with X=Data
Input X shape: (109610, 3)
Input X columns: ['unique_id', 'ds', 'y']
Real shape: (109610, 3)


Predicting: |          | 0/? [00:00<?, ?it/s]

Preds shape: (132360, 3)
Preds columns: ['unique_id', 'ds', 'CustomNBEATS']
Merged shape: (109610, 4)
Merged columns: ['unique_id', 'ds', 'y', 'CustomNBEATS']
Blocks_5_5_5: WMAE = 1599.15
🏃 View run Blocks_5_5_5 at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/22/runs/d0c60ff71e7c428e9498e8090c5b4b22
🧪 View experiment at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/22
  → New best! WMAE: 1599.15


In [ ]:
best_params_found

{'input_size': 52,
 'h': 40,
 'max_steps': 1500,
 'batch_size': 64,
 'stack_types': ['identity', 'trend', 'seasonality'],
 'n_blocks': [5, 5, 5],
 'n_polynomials': 2,
 'n_harmonics': 2,
 'learning_rate': 0.001,
 'random_seed': 42}

In [ ]:
print("\n4. Testing Learning Rates...")
learning_rates = [0.0005, 0.001, 0.002, 0.005]

for lr in learning_rates:
    params = best_params_found.copy()
    params['learning_rate'] = lr

    val_wmae, model = run_experiment(
        params,
        "NBEATS_Hyperparameter_Tuning",
        f"LR_{lr}"
    )

    if val_wmae < best_wmae:
        best_wmae = val_wmae
        best_params_found = params.copy()
        best_model = model
        print(f"  → New best! WMAE: {val_wmae:.2f}")


4. Testing Learning Rates...


INFO:lightning_fabric.utilities.seed:Seed set to 42


Minimum series length: 1
Input size requirement: 52
Fitting N-BEATS model with 3309 series...
Total data points: 311960


INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_steps=1500` reached.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


predict() called with X=Data
Input X shape: (109610, 3)
Input X columns: ['unique_id', 'ds', 'y']
Real shape: (109610, 3)


Predicting: |          | 0/? [00:00<?, ?it/s]

Preds shape: (132360, 3)
Preds columns: ['unique_id', 'ds', 'CustomNBEATS']
Merged shape: (109610, 4)
Merged columns: ['unique_id', 'ds', 'y', 'CustomNBEATS']
LR_0.005: WMAE = 1051689.20
🏃 View run LR_0.005 at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/22/runs/25e4d9f92ece470bbb2b8dec5fb70807
🧪 View experiment at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/22


In [ ]:
print("\n5. Testing Batch Sizes...")
batch_sizes = [32, 64, 128, 256]

for batch_size in batch_sizes:
    params = best_params_found.copy()
    params['batch_size'] = batch_size

    val_wmae, model = run_experiment(
        params,
        "NBEATS_Hyperparameter_Tuning",
        f"BatchSize_{batch_size}"
    )

    if val_wmae < best_wmae:
        best_wmae = val_wmae
        best_params_found = params.copy()
        best_model = model
        print(f"  → New best! WMAE: {val_wmae:.2f}")


5. Testing Batch Sizes...


INFO:lightning_fabric.utilities.seed:Seed set to 42


Minimum series length: 1
Input size requirement: 52
Fitting N-BEATS model with 3309 series...
Total data points: 311960


INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_steps=1500` reached.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


predict() called with X=Data
Input X shape: (109610, 3)
Input X columns: ['unique_id', 'ds', 'y']
Real shape: (109610, 3)


Predicting: |          | 0/? [00:00<?, ?it/s]

Preds shape: (132360, 3)
Preds columns: ['unique_id', 'ds', 'CustomNBEATS']
Merged shape: (109610, 4)
Merged columns: ['unique_id', 'ds', 'y', 'CustomNBEATS']
BatchSize_256: WMAE = 1612.66
🏃 View run BatchSize_256 at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/22/runs/4f912bd0d34e41c4baee15a9e7b227d1
🧪 View experiment at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/22


In [ ]:
print("\n6. Testing Training Steps...")
max_steps_options = [1000, 1500, 2000, 2500, 3000]

for max_steps in max_steps_options:
    params = best_params_found.copy()
    params['max_steps'] = max_steps

    wmae, model = run_experiment(
        params,
        "NBEATS_Hyperparameter_Tuning",
        f"Steps_{max_steps}"
    )

    if wmae < best_wmae:
        best_wmae = wmae
        best_params_found = params.copy()
        best_model = model
        print(f"  → New best! WMAE: {wmae:.2f}")


6. Testing Training Steps...


INFO:lightning_fabric.utilities.seed:Seed set to 42


Minimum series length: 1
Input size requirement: 52
Fitting N-BEATS model with 3309 series...
Total data points: 311960


INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_steps=3000` reached.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


predict() called with X=Data
Input X shape: (109610, 3)
Input X columns: ['unique_id', 'ds', 'y']
Real shape: (109610, 3)


Predicting: |          | 0/? [00:00<?, ?it/s]

Preds shape: (132360, 3)
Preds columns: ['unique_id', 'ds', 'CustomNBEATS']
Merged shape: (109610, 4)
Merged columns: ['unique_id', 'ds', 'y', 'CustomNBEATS']
Steps_3000: WMAE = 1620.44
🏃 View run Steps_3000 at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/22/runs/fce18af5fd17451e85ba0b240dc65aba
🧪 View experiment at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/22


In [ ]:
print(f"\nGenerating final submission with best parameters...")

full_train_df = preprocessor.transform(train)
w_full = full_train_df["IsHoliday"].map({True: 5, False: 1}).values
full_train_df = full_train_df.drop('IsHoliday', axis=1)

final_model = NBEATSModel(**best_params_found)
final_model.fit(full_train_df)

test_df = preprocessor.transform(test)
test_df = test_df.drop('IsHoliday', axis=1)

final_submission = generate_kaggle_submission(final_model, test_df, test)
final_submission.to_csv('nbeats_best_tuned_submission.csv', index=False)
print("Best submission saved as 'nbeats_best_tuned_submission.csv'")


Generating final submission with best parameters...


INFO:lightning_fabric.utilities.seed:Seed set to 42


Minimum series length: 1
Input size requirement: 52
Fitting N-BEATS model with 3331 series...
Total data points: 421570


INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_steps=1500` reached.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


predict() called with X=Data
Input X shape: (115064, 3)
Input X columns: ['unique_id', 'ds', 'y']
Real shape: (115064, 3)


Predicting: |          | 0/? [00:00<?, ?it/s]

Preds shape: (133240, 3)
Preds columns: ['unique_id', 'ds', 'CustomNBEATS']
Merged shape: (115064, 4)
Merged columns: ['unique_id', 'ds', 'y', 'CustomNBEATS']
Best submission saved as 'nbeats_best_tuned_submission.csv'


In [ ]:
best_params_found

{'input_size': 52,
 'h': 40,
 'max_steps': 1500,
 'batch_size': 64,
 'stack_types': ['identity', 'trend', 'seasonality'],
 'n_blocks': [5, 5, 5],
 'n_polynomials': 2,
 'n_harmonics': 2,
 'learning_rate': 0.001,
 'random_seed': 42}